In [ ]:
knitr::opts_chunk$set(echo = T,
                      warnings=F,
                      error=F,
                      message=F)

## Sissejuhatus

Siin on üks tekstiotsingu kasutusnäidis. Näiteks võib meid huvitada, kuidas kajastati eri energiaallikaid 20. sajandi alguses Eestis. Võimalike küsimuste hulk on suur, siin keskendume lihtsamaile neist. Näidise juures on koodinäidised, mis võimaldavad sarnaseid otsinguid dea.digar.ee avatud kogudest teha.

## Ligipääs

[dea.digar.ee](https://dea.digar.ee/) avatud materjalid on hoiustatud ETAIS serverisse. Neile pääseb ligi ETAIS serveri Jupyter keskkonna kaudu https://jupyter.hpc.ut.ee/. Praegu on ligipääsuks tehtud R-i pakett, mis 1) avab kerge vaevaga metaandmed, 2) võimaldab teha sihipäraseid valimeid tervikkogust, 3) võimaldab koondada tekste otsingusõnade alusel ja 4) võimaldab vaadata otsingute lähemat konteksti.

Kasutajanime saab küsida data@nlib.ee. Sisse logimisel töötavad ETAISi või UT arvutuskeskusega seotud kasutajanimed.

### Paketi käivitamine

Artiklite ligipääsuks tehtud käsud on vormistatud hetkel R-i paketina. Selle kasutamiseks tuleks avada Jupyteri keskkonnas uus Notebook, seades kerneliks R-i pakutud versiooni. Failide ligipääsuks tuleb paigaldada notebooki pakett digar.txts järgnevate käskudega. Kuna Jupyter keskkonnas on administratsiooniõigused piiratud, tuleb see pakett paigaldada kohalikku kataloogi. Teeme kõigepealt kataloogi R_pckg ja installime sinna digar.txts paketi. Muid pakette pole vaja uuendada. Seejärel käivitame installitud paketi library() käsuga, lisades parameetri installfailide asukoha kohta.

In [ ]:
dir.create("~/R_pckg")
remotes::install_github("peeter-t2/digar.txts",lib="~/R_pckg/",upgrade="never")
library(digar.txts,lib.loc="~/R_pckg/")

Andmetega mugavaks ringikäimiseks tuleb käivitada veel mõned paketid. Järgmises juhendis kasutame tidyverse pakette andmete muundamiseks ja tidytext lisapaketti lihtsamaks tekstitöötluseks.

In [ ]:
library(tidyverse)
library(tidytext)

## Andmed

Esimese asjana tahame me kätte saada ülevaate kollektsiooni sisust. Viimase versiooni kollektsiooni sisust loeb sisse käsk get_digar_overview(). Salvestame selle muutujasse all_issues. Ja vaatame seejärel esimest 5 rida seal.

In [ ]:
all_issues <- get_digar_overview()

In [ ]:
all_issues %>% head(5) %>% select(1:10) %>%  knitr::kable()

### Valimi loomine

Me võime valida välja oma valimi uurides kollektsiooni sisu põhjalikult. Siin näites võtame aluseks ajalehed, mis on ilmunud 1880 ja 1940 aasta vahel.

In [ ]:
subset <- all_issues %>%
    filter(DocumentType=="NEWSPAPER") %>%
    filter(year>1880&year<1940)

Vaatame valimi 5 esimest rida.

In [ ]:
subset %>% head(5) %>% select(1:10) %>% knitr::kable()

Selle kriteeriumi järgi leiame 626 erinevat lehte, kus kõige enam on Postimehe numbreid - 15363.

In [ ]:
subset %>% count(keyid,sort=T)

Et tagada tasakaalustatust valimis, valime välja ainult ühe lehe, millel on siin hea ajaline kate, Postimehe. Selleks saame täpsustada oma valimit seades piiranguks veel, et key peab võrduma nimega "postimeesew", mis on selle lehe kood andmebaasis. Võime vaadata jälle esimest 5 rida valimist, mis on nüüd Postimehe erinevad numbrid.

In [ ]:
subset <- all_issues %>%
    filter(DocumentType=="NEWSPAPER") %>%
    filter(year>1880&year<1940) %>%
    filter(keyid=="postimeesew")

In [ ]:
subset %>% head(5) %>% select(1:10) %>% knitr::kable()

Andmestikus on metaandmeid kokku kahel kihil. Esimesel kihil on kõikide ajalehenumbrite metainfo. Neid on kokku 353163. Edasi võime vaadata metainformatsiooni iga artikli kohta. See on jaotatud väiksematesse failidesse, et ei peaks kogu andmestikku korraga sisse lugema. Käsk get_subset_meta() kogub teatud alahulga artiklite kohta metainformatsiooni ja salvestab selle muutujasse.

Me saame edasiste analüüside lihtsustamiseks salvestada ta ka eraldi faili 'subset_meta_postimeesew1.tsv'

In [ ]:
subset_meta <- get_subset_meta(subset)
#write_tsv(subset_meta,"subset_meta_postimeesew1.tsv")

Soovi korral saame me lugeda selle andmestiku eraldi failist ja ei pea enam serverist seda küsima. Selleks veendume, et meie töökataloog on õiges kohas ja siis loeme muutujasse subset_meta andmed failist. Kui me võtsime need andmed juba serverist, siis pole failist lugemine meile hädavajalik.

In [ ]:
#subset_meta <- read_tsv("subset_meta_postimeesew1.tsv")

In [ ]:
subset_meta %>% head(5) %>% select(1:6) %>% knitr::kable()

## Valimist ülevaate saamine

Kui meil on olemas andmestiku metainfo ühes tabelis, võime proovida sellest mõningat ülevaadet saada. Vaatame, mitu sõna on valimis igal aastal ja seejärel kuidas need see sisuhulk jaotub artikli tüüpide vahel. Alustuseks vaatame mitu artiklit me valimisse saime.

In [ ]:
nrow(subset_meta)

In [ ]:
subset_meta %>% 
  group_by(year) %>% 
  summarise(words=sum(LogicalSectionTextWordCount)) %>% 
  ggplot(aes(x=year,y=words))+
  geom_col()

In [ ]:
subset_meta %>% 
  group_by(year,LogicalSectionType) %>% 
  summarise(words=sum(LogicalSectionTextWordCount)) %>% 
  ggplot(aes(x=year,y=words,fill=LogicalSectionType))+
  geom_col()
  

### Valimi põhjal vaheandmestike tegemine

Me saame salvestada meile olulise informatsiooni valimist eraldi muutujasse. Kui me teeme tekstiotsinguid, siis tihti huvitab meid, kui sagedasti esinevade meie otsingu tulemused valimis. Selle jaoks peame võrdlema oma otsingu tulemusi valimi enda suurusega. Teeme kaks ülevaatetabelit: 1) mitu artiklit oli valimis igal aastal, 2) mitu sõna oli valimis igal aastal. Neid kasutame veidi hiljem otsingutulemustega võrdlusel.

In [ ]:
subset_articlecounts <- subset_meta %>% 
  count(year)

subset_wordcounts <- subset_meta %>% 
  group_by(year) %>% 
  summarise(words=sum(LogicalSectionTextWordCount))

## Otsing

Üks levinumaid tekstikogude kasutusviise on tekstiotsing: me tahame leida tekste, mis on seotud mõne meie huvialaga ja näha, mida neis kirjutati, millal need ilmusid ning kuidas need seostuvad üldiste trendidega tekstikogus.

Praegu teeme me otsingud meie näidisküsimuse järgi. Meid huvitavad erinevad energiaallikad 20. sajandi alguses ja võime otsida mõnd, mida me teame, et seal peaks olema - näiteks auru, elektrit ja hobuseid. Teeme otsingud sõnaosale: otsime tekste, mis sisaldavad kuskil sees sõnaosa 'auru', 'elekt', 'hobu'. Kasutame ainult sõnaosi, et võimaldada vasteid erinevates käänetes ja liitsõnades.

Meie tekstiotsing (do_subset_search) salvestab leitud artiklid ühte faili. Kui tekste kasutada korduvalt siis tasub edaspidi otsing vahele jätta ja lugeda juba otse failist. Otsing meie valitud Postimehe vanadest lehtede `r nrow(subset_meta)` artiklist kestab umbes 2-3 minutit. Seejärel loeme need sealt välja ja seome metaandmetega (left_join). Lõpuks vaateme oma otsingusõna kontekstis +/- 30 tähemärki (get_concordances). Teeme seda kõigi kolme sõnaga ja salvestame tulemused eraldi muutujatesse.

In [ ]:
searchterm<- "auru"
searchfile<- "aur.txt"
do_subset_search(searchterm=searchterm, searchfile=searchfile,subset)
texts3 <- fread("aur.txt",header=F)[,.(id=V1,txt=V2)]
texts_w_meta3 <- texts3 %>% left_join(subset_meta %>% select(LogicalSectionID,LogicalSectionTitle,LogicalSectionType,LogicalSectionTextWordCount,MeanOCRAccuracyVol,docid,year),by=c("id"="LogicalSectionID"))
concs3 <- get_concordances(searchterm=searchterm,texts=texts3,before=30,after=30,txt="txt",id="id")

searchterm<- "elekt"
searchfile<- "elekter.txt"
do_subset_search(searchterm=searchterm, searchfile=searchfile,subset)
texts4 <- fread("elekter.txt",header=F)[,.(id=V1,txt=V2)]
texts_w_meta4 <- texts4 %>% left_join(subset_meta %>% select(LogicalSectionID,LogicalSectionTitle,LogicalSectionType,LogicalSectionTextWordCount,MeanOCRAccuracyVol,docid,year),by=c("id"="LogicalSectionID"))
concs4 <- get_concordances(searchterm=searchterm,texts=texts4,before=30,after=30,txt="txt",id="id")

searchterm<- "hobu"
searchfile<- "hobu.txt"
do_subset_search(searchterm=searchterm, searchfile=searchfile,subset)
texts5 <- fread("hobu.txt",header=F)[,.(id=V1,txt=V2)]
texts_w_meta5 <- texts5 %>% left_join(subset_meta %>% select(LogicalSectionID,LogicalSectionTitle,LogicalSectionType,LogicalSectionTextWordCount,MeanOCRAccuracyVol,docid,year),by=c("id"="LogicalSectionID"))
concs5 <- get_concordances(searchterm=searchterm,texts=texts5,before=30,after=30,txt="txt",id="id")

Võime seeläbi näiteks võrrelda - palju tulemusi üldse oli. Saame auru-tekste 22726, elektri-tekste 30262, hobu-tekste 54030.

In [ ]:
nrow(texts3)
nrow(texts4)
nrow(texts5)

Huvitav oleks teada, kuidas nad jagunevad korpuses ajas. Siin võime kokku lugeda mitu teksti igas aastas leiti ja lisada igale andmestikule tunnusväärtuse. Seejärel lisame need leidude numbrid järjestikku ning seome nad kõik ülevaatega valimist - mille me tegime paar lõiku tagasi. Teeme loodud andmestikust graafiku ja vaatame, kuidas leitud artiklite osakaal tervikkorpusest muutub ajas. Võime näha midagi, mida võisime juba ette aimata: aurujõud muutub vähem sagedasemaks samas kui elektri sagedus kasvab. Hobujõud püsivad aktuaalsena perioodi vältel (võimalik et see on ka osaliselt tingitud sellest, et autode reklaamis mängib olulist osa, mitu hobujõudu neil on).

In [ ]:
text_articlecounts3 <- texts_w_meta3 %>% 
  count(year) %>% mutate(set="aur")
text_articlecounts4 <- texts_w_meta4 %>% 
  count(year) %>% mutate(set="elekter")
text_articlecounts5 <- texts_w_meta5 %>% 
  count(year) %>% mutate(set="hobu")

text_articlecounts3 %>% 
  rbind(text_articlecounts4) %>% 
  rbind(text_articlecounts5) %>% 
  left_join(subset_articlecounts,by="year") %>% 
  ggplot(aes(x=year,y=n.x/n.y,color=set))+
  geom_line()

ggsave("plots/aur_elekter_hobu.png",width=6,height=5)

### Sõnade vaatamine

Edasi võib meid huvitada vaadata tulemusi lähemalt: kui kõigist teemadest räägiti terve aja vältel, siis millest konkreetsemalt seal räägiti. Ühe lihtsama küsimusena võime vaadata, milliseid energialiigi liitega sõnu kasutati. Selleks teeme meie sõnade lähikonteksti tekstijupid sõnatabeliteks, kus on üks sõna rea kohta. Ja võtame sealt välja kõik sõnad, mis sisaldavad neis meie otsingut. Vahepeal muudame ka kõik w-d v-deks, et üleminek w-lt v-le kirjaviisis ei segaks meie loendamist.

In [ ]:

wordcounts3 <- concs3 %>% 
  unnest_tokens(word,context) %>% 
  mutate(word=str_replace_all(word,"w","v")) %>% 
  count(word,sort=T)

auru <- wordcounts3 %>% 
  filter(str_detect(word,"auru"))

Võime vaadata esimest tulemust. Osad vasted tunduvad põnevamad: võime teha nende kohta märkuse edasiseks. Võtame näiteks "aurulaev", "aurukatel", "auruveski", "aurumasin" ja mõned veel.

In [ ]:
auru %>% head(50)

Teeme sama ka elektri ja hobu sõnadega. Kirjutame samuti välja ka sealt mõned nimed, mis meid huvitaks.

In [ ]:
wordcounts4 <- concs4 %>% 
  unnest_tokens(word,context) %>% 
  mutate(word=str_replace_all(word,"w","v")) %>% 
  count(word,sort=T)

elek <- wordcounts4 %>% 
  filter(str_detect(word,"elekt"))

In [ ]:
elek %>%
  head(50)

In [ ]:
wordcounts5 <- concs5 %>% 
  unnest_tokens(word,context) %>% 
  mutate(word=str_replace_all(word,"w","v")) %>% 
  count(word,sort=T)

hobu <- wordcounts5 %>% 
  filter(str_detect(word,"hobu"))

In [ ]:
  
hobu %>%
  head(50)

Nüüd võime tehaks tekstide põhjal miniuuringu. Otsime välja kõik sõnad, mis sisaldavad meile huvitavaid fraase ja vaatame, millal tekstid nende kohta ilmusid. Selleks seome meie sõnakontekstide tabeli taaskord metainfoga, mis sisaldab avaldamise aja informatsiooni ja kuvame neid eraldi graafikutes. Paneme punkti iga leiu kohta ja ajame neid veidi sassi. Nii saame lihtsa ülevaate sellest, millal mis teemast räägiti.

In [ ]:
concs_w_meta3 <- concs3 %>% left_join(subset_meta %>% select(LogicalSectionID,LogicalSectionTitle,LogicalSectionType,LogicalSectionTextWordCount,MeanOCRAccuracyVol,docid,year),by=c("id"="LogicalSectionID"))


In [ ]:
concs_w_meta4 <- concs4 %>% left_join(subset_meta %>% select(LogicalSectionID,LogicalSectionTitle,LogicalSectionType,LogicalSectionTextWordCount,MeanOCRAccuracyVol,docid,year),by=c("id"="LogicalSectionID"))


In [ ]:
concs_w_meta5 <- concs5 %>% left_join(subset_meta %>% select(LogicalSectionID,LogicalSectionTitle,LogicalSectionType,LogicalSectionTextWordCount,MeanOCRAccuracyVol,docid,year),by=c("id"="LogicalSectionID"))


In [ ]:


graafik<- concs_w_meta3 %>% 
  unnest_tokens(word,context) %>% 
  filter(str_detect(word,"aur")) %>% 
  mutate(word=str_replace(word,"w","v")) %>%
  mutate(type=str_extract(word,"aurulaev|aurukat|auruveski|aurumasin|aurulok|aurujõu|auruprits|veeaur|auruvärv")) %>% 
  filter(!is.na(type)) %>% 
  ggplot(aes(x=year, y=type))+
  geom_jitter(alpha=0.6)

graafik

ggsave("plots/aurugraafik1.png",graafik)

Meie valitud auru-sõnadega graafikult näeme, et aurulaevad saadavad peaaegu kogu perioodi, näidates väikest vähenemist 1930ndate keskpaigas. Aurukateldest hakatakse rääkima 1890nda aasta paiku. Auruveski on teemaks läbivalt, aga väga populaarne 1910ndatel ja aurulokkidest hakatakse rääkima 1930ndate teisel poolel.

In [ ]:


graafik<- concs_w_meta4 %>% 
  unnest_tokens(word,context) %>% 
  filter(str_detect(word,"elek")) %>% 
  mutate(word=str_replace(word,"w","v")) %>%
  mutate(type=str_extract(word,"elektritramm|hüdroelekt|elektrivalgus|elektrivabrik|elektrivool|elektrijaam|elektrimootor|elektrotehnika|elektrijõu|elektriväe|elektrifitseer|elektritriikrau|elektrikell|elektriplii")) %>% 
  filter(!is.na(type)) %>% 
  ggplot(aes(x=year, y=type))+
  geom_jitter(alpha=0.6)

graafik

ggsave("plots/elektrigraafik1.png",graafik)

Meie valitud elektri-sõnadega graafikult näeme, et elektrivalgusest räägitakse veidi kogu aja vältel, aga igapäevaseks teemaks muutub see 1909. aasta paiku, samamoodi ka elektrijaamadega. Kui elektrikell on nendega võrreldes pigem haruldane nähtus, siis ometi räägitakse sellest kogu perioodi vältel. Samas 1920ndad toovad jututeemaks uued tehnoloogiad: elektritramm, elektripliit, elektritriikraud ja ka üldisema termini elektrifitseerimine. Alates 1930ndate teisest poolest saab elektripliit juba igapäevaseks teemaks. Graafikult on näha ka tõenäoline sõnavaramuutus, kus elekrivägi asendub terminina elektrijõuga kuskil sajandivahetuse paiku.

In [ ]:


graafik<- concs_w_meta5 %>% 
  unnest_tokens(word,context) %>% 
  filter(str_detect(word,"hobu")) %>% 
  mutate(word=str_replace(word,"w","v")) %>%
  mutate(type=str_extract(word,"kahehobu|tööhobu|hobuseriist|hobusekasvatus|hobusejõu|hoburaudtee|hobuseruum|hobuseme|hobujõu|hobusetall|hobusevar|märahobu|ratsahobu")) %>% 
  filter(!is.na(type)) %>% 
  ggplot(aes(x=year, y=type))+
  geom_jitter(alpha=0.6)

graafik

ggsave("plots/hobugraafik1.png",graafik)

Meie valitud hobu-sõnadega graafikult näeme, et enamik teemasid on olnud jutuks läbivalt. 1920ndatel muutuvad hobusetallid tavalisemaks ja hakatakse rääkima hobujõust ja ka hobuseruumidest. 1890ndatest kuni 1910ndate lõpuni on oluliseks teemaks ka hoburaudtee, mis ilmselt elektritrammide ja üldise elektrifitseerimise protsessiga kaob.

### Kaassõnade analüüs

Viimaks võime vaadata, et millest siis nende sõnade kontekstis räägiti. Teeme sõnade vahetust kontekstist sõnaloendid, eemaldame stopsõnad, numbrid ja otsingusõnad endad ja vaatame, mis me tulemuseks saame. Stopsõnade loendina saame kasutada avalikke materjale, asetades faili nime kohale materjalide asukoha internetis url-na. Rohkem informatsiooni nende kohta võib näha siit http://dx.doi.org/10.15155/re-48.

In [ ]:
stopwords <- read_csv("https://datadoi.ee/bitstream/handle/33/78/estonian-stopwords.txt?sequence=1&isAllowed=y",col_names = F) %>% rename(word=X1)

In [ ]:

concs3 %>% 
  filter(str_detect(context,"elekt"))

wordsnostops3 <- concs3 %>% 
  unnest_tokens(word,context) %>% 
  filter(!str_detect(word,"auru")) %>% 
  filter(!str_detect(word,"[0-9]")) %>% 
  mutate(word=str_replace(word,"w","v")) %>% 
  anti_join(stopwords,by="word") %>% 
  count(word,sort=T) %>% 
  head(1000) %>% 
  mutate(set="auru")

In [ ]:
wordsnostops4 <- concs4 %>% 
  unnest_tokens(word,context) %>% 
  filter(!str_detect(word,"elekt")) %>% 
  filter(!str_detect(word,"[0-9]")) %>% 
  mutate(word=str_replace(word,"w","v")) %>% 
  anti_join(stopwords,by="word") %>% 
  count(word,sort=T) %>% 
  head(1000) %>% 
  mutate(set="elekter")

In [ ]:
wordsnostops5 <- concs5 %>% 
  unnest_tokens(word,context) %>% 
  filter(!str_detect(word,"hobu")) %>% 
  filter(!str_detect(word,"[0-9]")) %>% 
  mutate(word=str_replace(word,"w","v")) %>% 
  anti_join(stopwords,by="word") %>% 
  count(word,sort=T) %>% 
  head(1000) %>%
  mutate(set="hobu")

Võime vaadata, mis olid levinumad sõnad iga otsingusõna vahetus naabruses. Leidude põhjal tundub, et elektrist on räägitud eelkõige üürikorterite kontekstis. Aurust räägitakse ehk rahvusvaheliste aurulaevade ja kaubavahetuse kontekstis (saksa, inglise, vene, soome) ja samas ka elektri ja hobuse alternatiivide kontekstis - nt "wäikseid auru ja hobuse rehepeksmise masinaid", "ning 582 hobuse jõuline aurumasin", "aurujõuuga ja elektriwalgusega" või "elektri-aurulokid". Hobuste puhul räägitakse ostust-müügist ning seostuvast - vankrist, tööriistadest jne - summad rublades ja kroonides. 

In [ ]:
rbind(wordsnostops3,wordsnostops4,wordsnostops5) %>% 
  group_by(set) %>%
  mutate(row_number=row_number()) %>% 
  filter(row_number<21) %>% 
  ggplot(aes(x=set,y=row_number,label=word))+
  geom_text()

Võime ka vaadata, mille poolest eristuvad need rühmad teineteisest. Näeme veel enamaid viiteid välisriikidele auruga seotud tekstidest. Lisaks ka juttu sadamast, kaubast, laevast ja kaptenist (kpt). Elektri puhul domineerivad korteriüüri reklaamid ja kõik sellega seotud - küte, veevärk, sissekäigud, köögid, toad, mööbel. Hobuste puhul hobusega seotud sõnavara - mära, vanker, voorimees, ruun, tori, tõug. Lisaks on juttu ka varastatud hobustest ja lehmadest, mida müüdi ilmselt sarnastes kuulutustes.

In [ ]:
rbind(wordsnostops3,wordsnostops4,wordsnostops5) %>% 
  bind_tf_idf(word,set,n) %>% 
  arrange(desc(tf_idf)) %>% 
  group_by(set) %>%
  mutate(row_number=row_number()) %>% 
  filter(row_number<21) %>% 
  ggplot(aes(x=set,y=row_number,label=word))+
  geom_text()

## Kokkuvõte

Siin tõime ühe näidise sellest, kuidas ja milleks võiks dea.digar.ee avatud andmekogu kasutada. Praegu vaatasime energialiike, mida kasutati transpordis 20. sajandi esimeses pooles. Avatud kood annab võimaluse analüüsi kujundada täpselt enda soovide järgi. Kõige lihtsamalt on võimalik proovida teisi otsisõnud, teisi väljaandeid või otsida tulemusi mõnest teisest ajastust. Analoogsete otsingute tegemiseks piisab lihtsalt kui vahetada otsisõna, keerulisemate muudatuste tegemiseks on võimalik muuta ja kirjutada koodis uusi töötlussamme.

Avatud materjalidele on ligipääs avatud kõigile huvilistele - arvutiressursside kasutamiseks tuleb hankida endale küll kasutajanimi, selleks kirjutage data@nlib.ee. Tekstide töötlemisel aitavad kaasa raamatukogu materjalide kohta tehtud R-i pakett, mis aitab üles seatud failistruktuurist info kätte saada. Töötlemiseks kasutatavas Jupyter Notebook keskkonnas on võimalik kasutada nii R-i kui Pythonit, tuleb valida dokumendis õige kernel. 